In [1]:
import pandas as pd
import requests 
import json
from pandas.io.json import json_normalize
import os
import scipy.linalg as linalg
from pulp import *
import csv
import itertools
from tqdm import tqdm
import statsmodels.stats.moment_helpers as stats
from scipy import stats as scipy_stats
import scipy
import matplotlib.pyplot as plt
import math
import matplotlib.mlab as mlab
from datetime import datetime
import numpy as np
from random import randint
from collections import Counter
os.chdir('/home/valesco/Datasets/NFL_projs')
pd.set_option('display.max_columns', 106)
pd.set_option('display.max_rows', 100)

nfl_week = '2017_week_10'

In [9]:
url = 'http://www.fantasylabs.com/api/playermodel/1/11_9_2017/?modelId=1196314&projOnly=true' 

headers = { 'User-agent': 'Mozilla/5.0',
            'Cookie':'_cfduid=d2e9d0d941e292062b5792a57cd6183f11505095681; LD_U=http%3A%2F%2Fwww.fantasylabs.com%2F; __distillery=ddea8bf_c6fa751c-2767-47ec-9073-7092b00d479d-0862dfd0d-8888296cfa38-33df; LD_R=http%3A%2F%2Fwww.fantasylabs.com%2Fnfl%2Fcontests-dashboard%2F; flid=V2y0f5FbyE2AwjnR1hOc8Q; __zlcmid=iSgjnvnLj8Z3xC; _ga=GA1.2.993633943.1505095683; LD_T=8265517e-bdb6-44e0-fd38-0f5bcbdfb4a5; .AspNet.Cookies=B93JWWSNrNVPKs_Le38jv80AAO0pu_tYVJ5b_SdZ-lLrHmmVZ137ao4Q_SMvNyTsHBP4Byp0zB1F952tbkDf8j92zd39d_lI-wwSmVHOk3UmLiacvstbVYNkwsk3ECsn6OwZXkC0QUkRPIBt6b0VxG-oxWwWoig_3gDyOruvR1TSpRStZzOjGwzkZZME66bR8v2yCEo9oLcGXxKYdtRIfTGPz4WwbeYPpLjd_wkwkSzD0QoXXHXI5ODJE1XVGaOtwBReWfBNIP-eLJS1UO7E2xDRUrihMLnjVgmf9vk2097jHO5LSycea2B4Ued3HFzO4SZyK_jWG-U6ynz-O9R4arGOaLbIpyoM9Xv88uSUreOjR3X-Au6RMrnsneLoUUZhIi9Nqid4VeUUpC4B4rPtxmK4D1Pk2oH_b01epb06uzhAXXKfK3lEBSHaJbjkRB4nvrw8vO0qWDkrkuB6Xl4Mqw; hasmembership=True'
           }


response = requests.get(url, headers = headers)
json_data = response.json()

In [10]:
json_data

{'ContestGroupFantasyResults': [{'ContestGroupId': 17706,
   'FantasyResultId': 750889,
   'PlayerId': 1214},
  {'ContestGroupId': 17707, 'FantasyResultId': 750889, 'PlayerId': 1214},
  {'ContestGroupId': 17632, 'FantasyResultId': 750890, 'PlayerId': 1214},
  {'ContestGroupId': 17632, 'FantasyResultId': 750891, 'PlayerId': 2436},
  {'ContestGroupId': 17706, 'FantasyResultId': 750891, 'PlayerId': 2436},
  {'ContestGroupId': 17707, 'FantasyResultId': 750891, 'PlayerId': 2436},
  {'ContestGroupId': 17706, 'FantasyResultId': 750892, 'PlayerId': 3328},
  {'ContestGroupId': 17707, 'FantasyResultId': 750892, 'PlayerId': 3328},
  {'ContestGroupId': 17632, 'FantasyResultId': 750893, 'PlayerId': 3328},
  {'ContestGroupId': 17706, 'FantasyResultId': 750895, 'PlayerId': 6238},
  {'ContestGroupId': 17707, 'FantasyResultId': 750895, 'PlayerId': 6238},
  {'ContestGroupId': 17632, 'FantasyResultId': 750896, 'PlayerId': 6238},
  {'ContestGroupId': 17632, 'FantasyResultId': 750897, 'PlayerId': 7562},
  

In [11]:
week_all = json_normalize(json_data['PlayerModels'])
week_all.to_csv(nfl_week + '_projs.csv')
with open(nfl_week + '_projs.json', 'w') as outfile:
    json.dump(json_data['PlayerModels'], outfile)

In [12]:
week_dk = week_all.loc[week_all['Properties.SourceId'] == 4]
week_dk.head()

ActualPoints  Cnt  Correlation  CurrentExposure Exposure  FantasyResultId  \
7            0.0    0          0.0              0.0     None           751012   
21           0.0    0          0.0              0.0     None           750932   
23           0.0    0          0.0              0.0     None           750940   
24           0.0    0          0.0              0.0     None           750941   
30           0.0    0          0.0              0.0     None           750934   

   FirstPosition FullName IsExcluded IsLiked IsLocked  LineupCount  \
7             RB               False   False    False            0   
21            WR               False   False    False            0   
23            WR               False   False    False            0   
24            RB               False   False    False            0   
30            TE               False   False    False            0   

   MinExposure  PlayerId  Points Position  PositionCount  PositionId  \
7         None     26226     0.0       RB              1         102   
21        None      1214     0.0       WR              1         103   
23        None      8687     0.0       WR              1         103   
24        None      8732     0.0       RB              1         102   
30        None      3328     0.0       TE              1         104   

   Positions  ProjPoints Properties.ActualPoints  Properties.AdjYPA  \
7       [RB]         0.0                    None                NaN   
21      [WR]         0.0                    None               35.0   
23      [WR]         0.0                    None                NaN   
24      [RB]         0.0                    None                NaN   
30      [TE]         0.0                    None                NaN   

    Properties.AvgPts  Properties.Ceiling  Properties.CeilingPct  \
7                 4.8                11.7                     61   
21               15.8                28.6                     97   
23                9.7                19.0                     77   
24                8.0                15.6                     72   
30               12.6                19.5                     95   

   Properties.Confirmed  Properties.Consistency  Properties.EventId  \
7                  None                      25             3601450   
21                 None                      44             3601450   
23                 None                      38             3601450   
24                 None                      26             3601450   
30                 None                      64             3601450   

    Properties.EventTeamId  Properties.Exp  Properties.Exp_min  \
7                 36014501              -1                  -1   
21                36014501              -1                  -1   
23                36014501              -1                  -1   
24                36014501              -1                  -1   
30                36014501              -1                  -1   

    Properties.ExpectedSacksPct  Properties.FantasyResultId  Properties.Floor  \
7                            37                      751012               0.7   
21                           37                      750932               9.1   
23                           37                      750940               1.8   
24                           37                      750941               2.8   
30                           37                      750934               3.0   

    Properties.FloorPct  Properties.FloorPtPerDPct Properties.FullName  \
7                    26                         26                       
21                   86                         86                       
23                   35                         35                       
24                   48                         48                       
30                   60                         60                       

    Properties.Humidity  Properties.ImpPts Properties.InjuryStatus  \
7

In [13]:
cols = ['PlayerId',
 'Properties.Player_Name',
 'Salary',
 'TeamName',
 'Properties.Opposing_TeamFB',
 'Properties.AvgPts',
 'Properties.Floor',
 'Properties.FloorPct',
 'Properties.FloorPtPerDPct',
 'Properties.Ceiling',
 'Properties.CeilingPct',
 'Properties.Consistency',
 'Position',
 'PositionCount',
 'PositionId',
 'Positions',
 'Properties.AdjYPA',
 'Properties.EventTeamId',
 'Properties.ExpectedSacksPct',
 'Properties.ImpPts',
 'Properties.InterceptionPct',
 'Properties.IsProjected',
 'Properties.MktShrPct',
 'Properties.Month_FPOpp',
 'Properties.Month_FPSnap',
 'Properties.OffensiveSnapsMarketShare',
 'Properties.OppPlusMinusPct',
 'Properties.OpportunitiesRedZone',
 'Properties.OpportunitiesRedZone10',
 'Properties.OpportunitiesRedZone5',
 'Properties.PassINTPct',
 'Properties.PassSackPct',
 'Properties.PassTDPct',
 'Properties.PassingAttemptsRBPct',
 'Properties.PassingAttemptsTEPct',
 'Properties.PassingAttemptsWRPct',
 'Properties.PassingSuccessfulPct',
 'Properties.Plus_Minus',
 'Properties.Position',
 'Properties.PositionId',
 'Properties.Pro_Pct',
 'Properties.ProjPct',
 'Properties.ProjPlaysPct',
 'Properties.ProjPlusMinusPct',
 'Properties.PtPerDPct',
 'Properties.ReceivingTargetsMarketShare',
 'Properties.ReceivingTouchdownsMarketShare',
 'Properties.ReceivingTouchdownsRedZonePct',
 'Properties.ReceivingYardsMarketShare',
 'Properties.RedZoneSnaps',
 'Properties.RedZoneSnaps10',
 'Properties.RedZoneSnaps5',
 'Properties.RedZoneTouchdownPct',
 'Properties.RushingFantasyPct',
 'Properties.RushingSuccessfulAllowedPct',
 'Properties.RushingSuccessfulPct',
 'Properties.RushingSuccessfulPctRedZone',
 'Properties.RushingTouchdownsMarketShare',
 'Properties.RushingTouchdownsRedZonePct',
 'Properties.RushingYardsMarketShare',
 'Properties.SackPct',
 'Properties.Salary',
 'Properties.Salary_Movement',
 'Properties.Score',
 'Properties.Season_FPOpp',
 'Properties.Season_FPSnap',
 'Properties.Season_PPG',
 'Properties.Season_PPG_Percentile',
 'Properties.Season_Plus_Minus',
 'Properties.Season_Salary_Change',
 'Properties.Season_X0',
 'Properties.Season_X1',
 'Properties.Season_X2',
 'Properties.Site_Salary',
 'Properties.SourceId',
 'Properties.TakeawayPct',
 'Properties.Team',
 'Properties.TouchdownAllowedPct',
 'Properties.Upside',
 'Properties.Vegas',
 'Properties.YardsPerPassingAttempt',
 'Score']

week_dk = week_dk[cols]

In [14]:
new_cols = ['player_id',
 'name',
 'salary',
 'team',
 'opponent',
 'points_avg',
 'points_floor',
 'floor_pct',
 'floor_pt_per_dpct',
 'points_ceiling',
 'ceiling_pct',
 'consistency',
 'position',
 'position_count',
 'position_id',
 'positions',
 'adj_ypa',
 'event_team_id',
 'expected_sack_pct',
 'Properties.ImpPts',
 'Properties.InterceptionPct',
 'Properties.IsProjected',
 'Properties.MktShrPct',
 'Properties.Month_FPOpp',
 'Properties.Month_FPSnap',
 'Properties.OffensiveSnapsMarketShare',
 'Properties.OppPlusMinusPct',
 'Properties.OpportunitiesRedZone',
 'Properties.OpportunitiesRedZone10',
 'Properties.OpportunitiesRedZone5',
 'Properties.PassINTPct',
 'Properties.PassSackPct',
 'Properties.PassTDPct',
 'Properties.PassingAttemptsRBPct',
 'Properties.PassingAttemptsTEPct',
 'Properties.PassingAttemptsWRPct',
 'Properties.PassingSuccessfulPct',
 'Properties.Plus_Minus',
 'Properties.Position',
 'Properties.PositionId',
 'Properties.Pro_Pct',
 'Properties.ProjPct',
 'Properties.ProjPlaysPct',
 'Properties.ProjPlusMinusPct',
 'Properties.PtPerDPct',
 'Properties.ReceivingTargetsMarketShare',
 'Properties.ReceivingTouchdownsMarketShare',
 'Properties.ReceivingTouchdownsRedZonePct',
 'Properties.ReceivingYardsMarketShare',
 'Properties.RedZoneSnaps',
 'Properties.RedZoneSnaps10',
 'Properties.RedZoneSnaps5',
 'Properties.RedZoneTouchdownPct',
 'Properties.RushingFantasyPct',
 'Properties.RushingSuccessfulAllowedPct',
 'Properties.RushingSuccessfulPct',
 'Properties.RushingSuccessfulPctRedZone',
 'Properties.RushingTouchdownsMarketShare',
 'Properties.RushingTouchdownsRedZonePct',
 'Properties.RushingYardsMarketShare',
 'Properties.SackPct',
 'Properties.Salary',
 'Properties.Salary_Movement',
 'Properties.Score',
 'Properties.Season_FPOpp',
 'Properties.Season_FPSnap',
 'Properties.Season_PPG',
 'Properties.Season_PPG_Percentile',
 'Properties.Season_Plus_Minus',
 'Properties.Season_Salary_Change',
 'Properties.Season_X0',
 'Properties.Season_X1',
 'Properties.Season_X2',
 'Properties.Site_Salary',
 'Properties.SourceId',
 'Properties.TakeawayPct',
 'Properties.Team',
 'Properties.TouchdownAllowedPct',
 'Properties.Upside',
 'Properties.Vegas',
 'Properties.YardsPerPassingAttempt',
 'Score']

week_dk.columns = new_cols

In [15]:
week_dk.to_csv(nfl_week + '_dk_proj.csv', index = False)

week_dk = pd.read_csv(nfl_week + '_dk_proj.csv')

def home_away(x):
    if '@' in x:
        return 'away'
    else:
        return 'home'

proj_df = week_dk
cov_df = pd.read_csv('nfl_covariance_matrix.csv', index_col = 0)

#number of games in spreadsheet plus one
#num_of_games = 14


proj_df['matchup'] = tuple(zip(proj_df['team'], proj_df['opponent']))
#proj_df['salary'] = proj_df['salary'].apply(lambda x: x.replace('$',''))
#proj_df['salary'] = proj_df['salary'].apply(lambda x: float(x.replace('K', '')))
#proj_df['salary'] = proj_df['salary'].apply(lambda x: x * 1000)
proj_df['rank'] = proj_df.groupby(['team', 'position'])['points_avg'].rank(ascending = False, method = 'max')

proj_df['rank'].fillna(value = 9999, inplace = True)
proj_df['salary'].fillna(value = 9999, inplace = True)
proj_df['points_avg'].fillna(value = -9.999, inplace = True)
proj_df['rank'] = proj_df['rank'].apply(lambda x: str(int(x)))
proj_df['home_away'] = proj_df['opponent'].apply(lambda x: home_away(x))
proj_df['rank'] = proj_df['home_away'] + '_' + proj_df['position'] + proj_df['rank']

proj_df.to_csv('/home/valesco/Datasets/NFL_projs/' + nfl_week + '_proj_process.csv', index = False)
proj_df.head()

player_id           name  salary team opponent  points_avg  points_floor  \
0      26226   C.J. Prosise    3900  SEA     @ARI         4.8           0.7   
1       1214   Doug Baldwin    6400  SEA     @ARI        15.8           9.1   
2       8687  Tyler Lockett    4900  SEA     @ARI         9.7           1.8   
3       8732   Thomas Rawls    3400  SEA     @ARI         8.0           2.8   
4       3328   Jimmy Graham    5700  SEA     @ARI        12.6           3.0   

   floor_pct  floor_pt_per_dpct  points_ceiling  ceiling_pct  consistency  \
0         26                 26            11.7           61           25   
1         86                 86            28.6           97           44   
2         35                 35            19.0           77           38   
3         48                 48            15.6           72           26   
4         60                 60            19.5           95           64   

  position  position_count  position_id positions  adj_ypa  event_team_id  \
0       RB               1          102    ['RB']      NaN       36014501   
1       WR               1          103    ['WR']     35.0       36014501   
2       WR               1          103    ['WR']      NaN       36014501   
3       RB               1          102    ['RB']      NaN       36014501   
4       TE               1          104    ['TE']      NaN       36014501   

   expected_sack_pct  Properties.ImpPts  Properties.InterceptionPct  \
0                 37               8.10                        2.64   
1                 37              13.78                        2.64   
2                 37              10.34                        2.64   
3                 37               6.68                        2.64   
4                 37              13.14                        2.64   

  Properties.IsProjected  Properties.MktShrPct  Properties.Month_FPOpp  \
0                   True                    42                    0.00   
1                   True                    97                    1.84   
2                   True                    67                    1.20   
3                   True                    48                    0.45   
4                   True                    91                    2.36   

   Properties.Month_FPSnap  Properties.OffensiveSnapsMarketShare  \
0                     0.00                                  32.4   
1                     0.37                                  80.4   
2                     0.24                                  61.9   
3                     0.13                                  45.8   
4                     0.29                                  71.3   

   Properties.OppPlusMinusPct  Properties.OpportunitiesRedZone  \
0                          12                             0.69   
1                          47                             1.06   
2                          47                             0.69   
3                          12                             1.75   
4                          24                             1.56   

   Properties.OpportunitiesRedZone10  Properties.OpportunitiesRedZone5  \
0                               0.38                              0.13   
1                               0.56                              0.19   
2                               0.13                              0.06   
3                               1.13                              0.63   
4                               0.69                              0.63   

   Properties.PassINTPct  Properties.PassSackPct  Properties.PassTDPct  \
0                    NaN                     NaN                   NaN   
1                    0.0                     0.0                 100.0   
2                    NaN                     NaN                   NaN   
3                    NaN                     NaN                   NaN   
4                    NaN                     NaN                   NaN   

   Properties.PassingAttemptsRBPct

In [16]:
players = list(proj_df['name'].values)
salary = list(proj_df['salary'].values)
points = list(proj_df['points_avg'].values)
position = list(proj_df['position'].values)

player_dict = dict((z[0], list(z[1:])) for z in zip(players, salary, points, position))


In [17]:
away_teams = proj_df['team'].loc[proj_df['home_away'] == 'away'].unique()

print(away_teams)

player_cols = []
count = 0

for team in away_teams:
    temp1 = proj_df.loc[proj_df['team'] == team]
    temp2 = proj_df.loc[proj_df['opponent'] == team]
    temp_df = pd.concat([temp1, temp2], axis = 0)
    
    cols = cov_df.columns

    player_ls = []
    for c in cols:
        player = pd.DataFrame(temp_df.loc[temp_df['rank'] == c])
        
        if len(player) < 1:
            name = 'Not Available_' + str(count)
            count += 1
        else:
            name = player.iloc[0]['name']
        player_ls.append(name)
        
    player_cols.extend(player_ls)
    

arr_cov = np.asarray(cov_df)
for i in range(1, 13):
    arr_new = np.asarray(cov_df)
    arr_cov = linalg.block_diag(arr_cov, arr_new)
    
comp_cov_df = pd.DataFrame(data = arr_cov, index = player_cols, columns = player_cols)
comp_cov_df.head()

['SEA' 'PIT' 'MIN' 'LAC' 'NO' 'GB' 'CIN' 'NYJ' 'CLE' 'HOU' 'NYG' 'DAL' 'NE'
 'MIA']


ValueError: Shape of passed values is (208, 208), indices imply (224, 224)

In [18]:
position_std = {'QB': 8.096014, 'WR': 9.813933, 'RB': 8.702397, 'TE': 8.096014, 'D': 6.09265}
position_mu = {'QB': 19.861207, 'WR': 12.67457, 'RB': 12.900904, 'TE': 12.50152, 'D': 7.447265}

In [19]:
main_slate = pd.read_csv('/home/valesco/Datasets/NFL_projs/' + nfl_week + '_proj_process.csv')


players = list(main_slate['name'].values)
salary = list(main_slate['salary'].values)
points = list(main_slate['points_avg'].values)
position = list(main_slate['position'].values)

player_dict = dict((z[0], list(z[1:])) for z in zip(players, salary, points, position))

In [20]:
# Set position lists
qbs = []
wrs = []
rbs = []
tes = []
dsts = []
flexs = [] 

for player, ls in player_dict.items():
    if ls[2] == 'QB':
        if ls[1] > 12:
            qbs.append(player)
    if ls[2] == 'WR':
        if ls[1] > 7:
            wrs.append(player)
    if ls[2] == 'RB':
        if ls[1] > 8:
            rbs.append(player)
    if ls[2] == 'TE':
        if ls[1] > 5:
            tes.append(player)
    if ls[2] == 'D':
        if ls[1] > 4:
            dsts.append(player)
    if ls[2] == 'WR' or ls[2] == 'TE' or ls[2] == 'RB':
        if ls[1] > 6:
            flexs.append(player)
        

In [21]:
#select random starting team

def create_first_team(mydict, **kwargs):
    while True:
        qb = qbs[randint(0,len(qbs) - 1)]
        wr1 = wrs[randint(0,len(wrs) - 1)]
        wr2 = wrs[randint(0,len(wrs) - 1)]
        wr3 = wrs[randint(0,len(wrs) - 1)]
        rb1 = rbs[randint(0,len(rbs) - 1)]
        rb2 = rbs[randint(0,len(rbs) - 1)]
        te = tes[randint(0,len(tes) - 1)]
        d = dsts[randint(0,len(dsts) - 1)]
        flex = flexs[randint(0,len(flexs) - 1)]

        player_list =  [qb, rb1, rb2, wr1, wr2, wr3, te, flex, d]
            
        team_salary = 0

        for player in player_list:
            team_salary += player_dict[player][0]

        duplicates = Counter(player_list)

        if team_salary <= 50000 and team_salary >= 47000 and sum(duplicates.values()) == 9:
            for key, value in mydict.items():
                if key == 'QB':
                    z = 0
                elif key == 'RB1':
                    z = 1
                elif key == 'RB2':
                    z = 2
                elif key == 'WR1': 
                    z = 3
                elif key == 'WR2':
                    z = 4
                elif key == 'WR3':
                    z = 5
                elif key == 'TE':
                    z = 6
                elif key == 'FLEX':
                    z = 7
                elif key == 'DST' or key == 'D' or key == 'DEF':
                    z = 8
                else:
                    print('Waaat')

                player_list[z] = value
            break
                
    return player_list

In [26]:
#Simulated annealing
def update_temp(i, t):
    temp = t / log(i)
    return temp

def cost(ls):
    qb = ls[0]
    rb1 = ls[1]
    rb2 = ls[2]
    wr1 = ls[3]
    wr2 = ls[4]
    wr3 = ls[5]
    te = ls[6]
    flex = ls[7]
    dst = ls[8]
    flex_pos = player_dict[flex][2]
    
    qb_mu = player_dict[qb][1]
    wr1_mu = player_dict[wr1][1]
    wr2_mu = player_dict[wr2][1]
    wr3_mu = player_dict[wr3][1]
    rb1_mu = player_dict[rb1][1]
    rb2_mu = player_dict[rb2][1]
    te_mu = player_dict[te][1]
    dst_mu = player_dict[dst][1]
    flex_mu = player_dict[flex][1]
    
    qb_std = position_std['QB']
    wr_std = position_std['WR']
    rb_std = position_std['RB']
    te_std = position_std['TE']
    dst_std = position_std['D']
    
    if flex_pos == 'WR':
        flex_std = wr_std
    elif flex_pos == 'RB':
        flex_std = rb_std
    elif flex_pos == 'TE':
        flex_std = te_std
    else:
        print('Waat')
        
    #create covariance matrix
    corr_array = []
    
    
    for player1 in ls:
        temp_ls = []
        for player2 in ls:
            try:
                corr = comp_cov_df[player1][player2]
            except:
                corr = 0
            temp_ls.append(corr)
            
        corr_array.append(temp_ls)
        
    corr_matrix = np.array(corr_array)
    cov_matrix = stats.corr2cov(corr_matrix, [qb_std, wr_std, wr_std, wr_std, rb_std, rb_std, te_std,
                                             dst_std, flex_std])
    cov_sum = 0
    
    for i in range(9):
        for x in range(9):
            if i > x:
                cov_sum += cov_matrix[x,i]
    
    #Calculate team variance
    
    team_var = (qb_std ** 2 + wr_std ** 2 + wr_std ** 2 + wr_std ** 2 + rb_std ** 2 + rb_std ** 2 +
                te_std ** 2 + dst_std ** 2 + flex_std ** 2 + 2 * cov_sum)
    
    team_mu = qb_mu + wr1_mu + wr2_mu + wr3_mu + rb1_mu + rb2_mu + te_mu + dst_mu + flex_mu
    
    team_ppf = scipy_stats.norm(team_mu, np.sqrt(team_var)).ppf(.95)
    
    return team_ppf

def random_except(length, except_ls):
    while True:
        r = randint(0, length - 1 )
        if r not in except_ls:
            return r
            break

    
    
def create_team(ls, except_ls, player_except):
    counter = 0
    while True:
        temp_best = ls[:]
        r = random_except(len(temp_best), except_ls)

        if r == 0:
            new_player = qbs[randint(0,len(qbs) - 1)]
        elif r > 0 and r <= 2:
            new_player = rbs[randint(0, len(rbs) - 1)]
        elif r > 2 and r <= 5:
            new_player = wrs[randint(0, len(wrs) - 1)]
        elif r == 6:
            new_player = tes[randint(0, len(tes) - 1)]
        elif r == 7:
            new_player = flexs[randint(0, len(flexs) - 1)]
        elif r == 8:
            new_player = dsts[randint(0, len(dsts) - 1)]
        else:
            print('Waaat')

        temp_best[r] = new_player

        team_salary = 0

        for player in temp_best:
            team_salary += player_dict[player][0]

        duplicates = Counter(temp_best)

        if team_salary <= 50000 and team_salary >= 47000 and len(duplicates.values()) == 9:
                break
                
        counter += 1
        
        if counter > 1000:
            temp_best = create_first_team(player_except)
            break
            
    return temp_best

final_teams = []


except_ls = []
player_except = {}

for z in tqdm(range(50)):
    player_list = create_first_team(player_except)

    max_iters = 2000
    best_team = player_list[:]
    current_best = player_list[:]
    temp = 100
    temp_change = .995
    ppf_list = []
    temp_ls = []
    count = 0

    for i in range(max_iters):
        new_team = create_team(current_best, except_ls, player_except)   

        cost_new = cost(new_team)
        cost_curr = cost(current_best)

        if cost_new > cost_curr:
            current_best = new_team[:]
            ppf_list.append([i, cost_new])
        else:
            temp = temp * temp_change
            if temp < 0:
                temp = 100 - count
                if count < 100:
                    count += 7
            r = randint(1,120)

            if r < temp:
                temp_ls.append([r, temp])
                current_best = new_team[:]
                ppf_list.append([i, cost_new])

    pff_current = cost(current_best)
    current_best.append(pff_current)
    final_teams.append(current_best)
    print(current_best)


final_df = pd.DataFrame(columns = ['QB', 'RB', 'RB', 'WR', 'WR', 'WR', 'TE', 'FLEX', 'DST', 'PPF'])


for a, team in enumerate(final_teams):
    final_df.loc[a] = final_teams[a]

#title_name = 'final_df' + str(k + 4) + '.csv'  
#final_df.sort_values('PPF', ascending = False, inplace = True)
#final_df.to_csv(title_name)

  2%|▏         | 1/50 [00:03<02:35,  3.17s/it]

['Ryan Fitzpatrick', 'Bilal Powell', 'Todd Gurley', 'Michael Thomas', 'Adam Humphries', 'Julio Jones', 'Jack Doyle', 'Mohamed Sanu', 'Detroit Defense', 177.27164812052391]


  4%|▍         | 2/50 [00:06<02:33,  3.21s/it]

['Ryan Fitzpatrick', 'Chris Thompson', 'Todd Gurley', 'Doug Baldwin', 'Mohamed Sanu', 'Marvin Jones', 'Austin Hooper', 'Jordan Howard', 'Detroit Defense', 174.92939140465597]


  6%|▌         | 3/50 [00:09<02:32,  3.24s/it]

...

['Russell Wilson', 'Carlos Hyde', 'Jordan Howard', 'Doug Baldwin', 'Michael Thomas', 'Adam Humphries', 'Austin Hooper', 'Christian McCaffrey', 'Detroit Defense', 178.929391404656]


 98%|█████████▊| 49/50 [02:38<00:03,  3.20s/it]

['Ryan Fitzpatrick', 'Jordan Howard', 'Chris Thompson', 'Julio Jones', 'Sterling Shepard', 'Jarvis Landry', 'Vernon Davis', 'Mohamed Sanu', 'Detroit Defense', 172.3716481205239]


100%|██████████| 50/50 [02:42<00:00,  3.21s/it]

['Russell Wilson', "Le'Veon Bell", 'Joe Mixon', 'Antonio Brown', 'Mohamed Sanu', 'Adam Humphries', 'Garrett Celek', 'Bilal Powell', 'LA Rams Defense', 179.12939140465599]


In [25]:
final_teams[0]

['Ryan Fitzpatrick',
 'LeSean McCoy',
 'Carlos Hyde',
 'Corey Davis',
 'Sterling Shepard',
 'Doug Baldwin',
 'Vernon Davis',
 'Jordan Howard',
 'Detroit Defense']

In [29]:
final_df = pd.DataFrame(columns = ['QB', 'RB1', 'RB2', 'WR1', 'WR2', 'WR3', 'TE', 'FLEX', 'DST', 'PPF'])


for i, team in enumerate(final_teams):
    final_df.loc[i] = final_teams[i]
    
#final_df.to_pickle('week5_ppf_lineups.p')

In [30]:
final_df.sort_values('PPF', ascending = False, inplace = True)
#final_df.to_csv('final_carr_amari.csv')
final_df.head(40)

QB                  RB1                  RB2  \
22    Russell Wilson          Carlos Hyde        Jordan Howard   
12        Cam Newton          Todd Gurley          Carlos Hyde   
31    Russell Wilson          Carlos Hyde         LeSean McCoy   
25  Matthew Stafford         Le'Veon Bell         Bilal Powell   
32  Ryan Fitzpatrick          Carlos Hyde         Le'Veon Bell   
46        Cam Newton          Carlos Hyde         Bilal Powell   
49    Russell Wilson         Le'Veon Bell            Joe Mixon   
47    Russell Wilson          Carlos Hyde        Jordan Howard   
29  Matthew Stafford        Jordan Howard         Le'Veon Bell   
20  Matthew Stafford         Bilal Powell          Todd Gurley   
39    Russell Wilson          Carlos Hyde         Bilal Powell   
43      Tyrod Taylor         Le'Veon Bell            Joe Mixon   
34    Russell Wilson          Carlos Hyde        Jordan Howard   
5   Matthew Stafford         Duke Johnson         Le'Veon Bell   
13  Matthew Stafford          Carlos Hyde            Joe Mixon   
26      Tyrod Taylor          Carlos Hyde         Bilal Powell   
41    Marcus Mariota          Todd Gurley         Bilal Powell   
33  Matthew Stafford          Carlos Hyde         Bilal Powell   
30  Matthew Stafford         Bilal Powell        Jordan Howard   
17  Matthew Stafford          Carlos Hyde         Bilal Powell   
37  Matthew Stafford            Joe Mixon          Todd Gurley   
0   Ryan Fitzpatrick         Bilal Powell          Todd Gurley   
21  Matthew Stafford         Bilal Powell            Joe Mixon   
28  Matthew Stafford        Jordan Howard            Joe Mixon   
15  Matthew Stafford         LeSean McCoy          Todd Gurley   
44  Ryan Fitzpatrick          Carlos Hyde          Todd Gurley   
3   Matthew Stafford  Christian McCaffrey          Carlos Hyde   
2   Ryan Fitzpatrick            Joe Mixon        Jordan Howard   
45  Ryan Fitzpatrick          Carlos Hyde  Christian McCaffrey   
11  Matthew Stafford         LeSean McCoy            Joe Mixon   
14  Ryan Fitzpatrick         Bilal Powell          Todd Gurley   
27  Matthew Stafford         Bilal Powell          Carlos Hyde   
38  Ryan Fitzpatrick          Todd Gurley            Joe Mixon   
35  Ryan Fitzpatrick      Devonta Freeman        Jordan Howard   
4   Matthew Stafford            Joe Mixon          Todd Gurley   
23        Cam Newton          Carlos Hyde         Bilal Powell   
10  Matthew Stafford         Bilal Powell            Joe Mixon   
16  Matthew Stafford         Duke Johnson         Le'Veon Bell   
8   Matthew Stafford            Joe Mixon         Bilal Powell   
1   Ryan Fitzpatrick       Chris Thompson          Todd Gurley   

                 WR1               WR2               WR3              TE  \
22      Doug Baldwin       Marqise Lee        A.J. Green   Cameron Brate   
12     Antonio Brown       Corey Davis    Adam Humphries    Vernon Davis   
31      Doug Baldwin       Julio Jones    Adam Humphries   Garrett Celek   
25       Corey Davis      Mohamed Sanu    DeSean Jackson   Austin Hooper   
32      Mohamed Sanu    Adam Humphries       Julio Jones      Jack Doyle   
46      Doug Baldwin       Corey Davis       Julio Jones   Garrett Celek   
49     Antonio Brown      Mohamed Sanu    Adam Humphries   Garrett Celek   
47      Doug Baldwin    Michael Thomas    Adam Humphries   Austin Hooper   
29    DeSean Jackson       Cooper Kupp    Adam Humphries    Vernon Davis   
20      Doug Baldwin      Keenan Allen      Mohamed Sanu   Austin Hooper   
39    Michael Thomas      Mohamed Sanu       Corey Davis     Evan Engram   
43        A.J. Green      Doug Baldwin       Corey Davis   Austin Hooper   
34    Adam Humphries    Michael Thomas        A.J. Green     Tyler Kroft   
5       Doug Baldwin       Corey Davis       Julio Jones   Austin Hooper   
13      Mohamed Sanu        A.J. Green      Doug Baldwin   Austin Hooper   
26      Doug Baldwin       Julio Jones    DeSean Jackson      Jack Doyle   
41      Doug Baldwi

In [34]:
final_df.groupby('QB').mean().sort_values('PPF', ascending = False)

PPF
QB                        
Case Keenum     178.555571
Tyrod Taylor    176.550255
Philip Rivers   176.312825
Blake Bortles   176.159090
Marcus Mariota  175.589615
Brett Hundley   174.926859
Tom Brady       174.598448
Kirk Cousins    174.358524
Carson Wentz    174.245887
Matt Ryan       173.858544
Russell Wilson  173.617171
Drew Brees      173.608853
Alex Smith      173.354298

In [33]:
pos_list = ['QB', 'RB1', 'RB2', 'WR1', 'WR2', 'WR3', 'TE', 'FLEX', 'DST']
grouped_df = final_df.groupby(pos_list[0]).mean()

for position in pos_list[1:]:
    grouped_df = grouped_df.append(final_df.groupby(position).mean())

grouped_df.reset_index(inplace = True)
final_grouped = grouped_df.groupby('index').mean()
final_grouped.reset_index(inplace = True)
final_grouped.columns = ['player', 'ppf']

final_grouped.sort_values('ppf', ascending = False, inplace = True)
final_grouped['rank'] = final_grouped['ppf'].rank(ascending = False)

final_grouped

player         ppf  rank
0        Adam Thielen  189.349202   1.0
30  Leonard Fournette  189.024671   2.0
14    Devonta Freeman  188.610264   3.0
8         Case Keenum  188.547297   4.0
41       Travis Kelce  188.505950   5.0
4     Arizona Defense  188.399117   6.0
12     DeSean Jackson  188.387287   7.0
39           Ted Ginn  188.196520   8.0
28       Kyle Rudolph  188.029667   9.0
25        Kareem Hunt  187.830548  10.0
3       Antonio Brown  187.811702  11.0
16         Drew Brees  187.739412  12.0
31        Mark Ingram  187.689996  13.0
32   Michael Crabtree  187.683091  14.0
36      Ricardo Louis  187.672236  15.0
9         Chris Hogan  187.642968  16.0
42        Tyreek Hill  187.614815  17.0
22         John Brown  187.585979  18.0
7       Cameron Brate  187.264447  19.5
5     Atlanta Defense  187.264447  19.5
29       Lamar Miller  187.259345  21.0
33     Michael Thomas  187.230547  22.0
10      Davante Adams  187.171895  23.0
13         Derek Carr  187.100394  24.0
1        Alvin Kamara  187.032328  25.0
23        Jordan Reed  187.021946  26.0
40          Tom Brady  186.971186  27.0
43        Zach Miller  186.682662  28.0
2        Amari Cooper  186.676480  29.0
37     Rob Gronkowski  186.669388  30.0
6   Baltimore Defense  186.572993  31.0
38     Taylor Gabriel  186.410381  32.0
15        Doug Martin  186.371499  33.0
35      Philip Rivers  186.336121  34.5
26       Keenan Allen  186.336121  34.5
11    DeAndre Hopkins  185.934206  36.0
19    Jamison Crowder  185.887685  37.0
34         Mike Evans  185.756979  38.0
20     Javorius Allen  185.235792  39.0
18     Jameis Winston  185.210029  40.0
21   Jermaine Gresham  185.104393  41.0
17        Golden Tate  182.844926  42.0
24        Julio Jones  182.713354  43.0
27        Kevin Hogan  181.564342  44.0

In [55]:
final_grouped['points_to_minus'] = np.linspace(1, 0, len(final_grouped)) * 1

In [60]:
players_in_grouped = final_grouped['player'].values

for key in player_dict.keys():
    if key in players_in_grouped:
        points_to_subtract = final_grouped['points_to_minus'].loc[final_grouped['player'] == key].values[0]
        player_dict[key][1] = player_dict[key][1] - points_to_subtract
    else:
        player_dict[key][1] += .10

Tyreek Hill
Antonio Brown
Rob Gronkowski
Jermaine Gresham
Philip Rivers
Mike Evans
Zach Miller
Taylor Gabriel
Ted Ginn
Jameis Winston
Amari Cooper
Doug Martin
Keenan Allen
Mark Ingram
Golden Tate
Michael Crabtree
Case Keenum
DeAndre Hopkins
Javorius Allen
Derek Carr
Julio Jones
Arizona Defense
Tom Brady
Travis Kelce
Jordan Reed
Ricardo Louis
DeSean Jackson
Kyle Rudolph
Leonard Fournette
Baltimore Defense
Devonta Freeman
Jamison Crowder
Chris Hogan
Kevin Hogan
Cameron Brate
Davante Adams
Drew Brees
Kareem Hunt
Alvin Kamara
Atlanta Defense
Adam Thielen
Michael Thomas
John Brown
Lamar Miller


In [71]:
track_points_df = pd.DataFrame()
track_points_df['player'] = players
track_points_df['points_start'] = points
track_points_df

player  points_start
0          Arizona Defense           9.0
1          Atlanta Defense           9.0
2        Baltimore Defense          10.0
3          Chicago Defense           4.0
4        Cleveland Defense           4.0
5          Detroit Defense           4.0
6        Green Bay Defense           5.0
7          Houston Defense           8.0
8     Jacksonville Defense           8.0
9      Kansas City Defense           6.0
10           Miami Defense           2.0
11       Minnesota Defense           3.0
12     New England Defense           7.0
13     New Orleans Defense           6.0
14         NY Jets Defense           2.0
15         Oakland Defense           7.0
16      Pittsburgh Defense           4.0
17     LA Chargers Defense           6.0
18   San Francisco Defense           3.0
19         LA Rams Defense           5.0
20       Tampa Bay Defense           7.0
21      Washington Defense           7.0
22           Blake Bortles          12.0
23               Tom Brady          25.0
24              Drew Brees          24.0
25              Derek Carr          19.0
26            Kirk Cousins          19.0
27              Jay Cutler          14.0
28              Joe Flacco          16.0
29             Brian Hoyer          16.0
30             Case Keenum          19.0
31             Josh McCown          16.0
32           Carson Palmer          19.4
33           Philip Rivers          21.0
34           Aaron Rodgers          22.2
35      Ben Roethlisberger          16.9
36               Matt Ryan          21.5
37              Alex Smith          18.8
38        Matthew Stafford          19.3
39          Jameis Winston          19.8
40             Kevin Hogan          18.0
41              Jared Goff          14.0
42          Deshaun Watson          21.4
43          Mitch Trubisky          13.7
44            Le'Veon Bell          21.0
45          Travaris Cadet           2.9
46          Isaiah Crowell           8.5
47        Benny Cunningham           4.1
48         Andre Ellington          12.6
49              Matt Forte           8.6
..                     ...           ...
157        Jermaine Kearse          11.3
158          Jeremy Kerley           8.1
159          Jarvis Landry          15.3
160            Marqise Lee           9.8
161          Jeremy Maclin          10.8
162           Jordy Nelson          14.0
163  Cordarrelle Patterson           4.6
164         Terrelle Pryor          13.0
165       Aldrick Robinson           3.9
166           Willie Snead           6.0
167           Kenny Stills           8.4
168            Golden Tate          16.0
169           Adam Thielen          16.0
170      De'Anthony Thomas           2.6
171           Mike Wallace           9.5
172          Sammy Watkins           9.1
173          Nick Williams           4.6
174          Albert Wilson           8.6
175           Robert Woods           8.7
176         Kendall Wright           8.2
177           Seth Roberts           5.9
178           Amari Cooper          14.0
179        Jamison Crowder          12.0
180           Justin Hardy           6.3
181         Adam Humphries           6.5
182               TJ Jones           4.1
183            Tre McBride           4.2
184        Jamarcus Nelson           7.7
185       Breshad Perriman           3.7
186         Kasen Williams           3.9
187        Tyrell Williams          10.2
188            Will Fuller          11.0
189         Michael Thomas          16.5
190         Jalin Marshall           3.0
191            Tyreek Hill          16.0
192      Demarcus Robinson           3.2
193          Leonte Carroo           6.7
194         Robby Anderson          10.1
195       Laquon Treadwell           6.2
196        Rashard Higgins           7.1
197           Josh Doctson           7.8
198           Jakeem Grant           6.0
199          Ricardo Louis          12.0
200           Chris Godwin           3.0
201    Juju Smith-Schuster           8.1
202            Keelan Cole           4.2
20

In [73]:
player_dict['Atlanta Defense']

[3500, 9.0, 'D']